In [1]:
# !pip install geopandas
# !pip install pgeocode
# !pip install folium
# !pip install pyshp
# !pip install haversine
# !pip install k-means-constrained
# !pip install k-means-constrained --target /opt/conda/lib/python3.8/site-packages
# !pip install --upgrade numpy --target /opt/conda/lib/python3.8/site-packages

In [1]:
import geopandas as gpd
import fiona

In [2]:
# 1) Get fake jobs for zipcodes in Orlando
# 2) Get problem descriptions for the jobs and predict parts START HERE
# 3) Create part stock list - top 10 model ice maker kits
# 4) Flag same day fix
# 5) run against current availibility mapping with agents

In [3]:
import warnings
warnings.filterwarnings("ignore")

In [4]:
import random
import sqlalchemy, os
import pandas as pd
import numpy as np
np.random.seed(201912)
import matplotlib.pyplot as plt
from datetime import datetime as dt
import pickle
from retail_toolkit import atlas
from retail_toolkit import credential_manager as cm
from numpy import average
import time

In [5]:
import requests
import json
from collections import Counter
from random import choices

In [6]:
import folium
from folium import plugins
# import geopandas as gpd
from folium.plugins import HeatMap
from shapely.geometry import Point, Polygon
import shapefile
from IPython.display import display

In [7]:
from k_means_constrained import KMeansConstrained

In [8]:
import pgeocode
from haversine import haversine, Unit
from kneed import KneeLocator

In [9]:
# Applying simple kmeans
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score, silhouette_samples
import matplotlib.pyplot as plt

In [63]:
# import get_coverage
import color_scheme
mapping = color_scheme.create_mapping()

In [11]:
def get_demand():
    presto_connection =  atlas.Presto(environment = 'presto://{}:{}@atlas-workbench-presto.atlas.prd.aws.asurion.net:18443/hive').connect()
    sql = """
    select distinct
        sj.service_order_id ,
        so.service_order_number,
        sj.service_job_type_id ,
        sj.payment_type ,
        sj.sj_program_id ,
        sj.external_reference_number ,
        sj.crm_number ,
        sj.service_job_id ,
        sj.service_job_number ,
        sj.service_job_status ,
        sj.service_job_sub_status ,
        sj.service_job_date,
        sj.service_job_source ,
        sj.service_request_type_code ,
        sj.technician_routing_status ,
        sj.technician_routing_message ,
        sj.route_order_number ,
        sj.scheduled_service_date,
        coalesce(o.orig_sched_dt, sj.scheduled_service_date) orig_service_dt ,
        sj.problem_description ,
        sj.service_explanation ,
        sj.technician_id ,
        rs.retailer_store_name,
        sprd.model_number,
        sprd.model_version,
        sprd.serial_number,
        sprd.internal_brand_code ,
        sprd.purchase_date ,
        sprd.purchase_price ,
        sprd.manufacturer ,
        sjpl.description industry,
        ftf.min_tech_arrival_dt,
        ftf.min_complete_dt,
        cus.address_line_1 addr_line_1,
        cus.address_city,
        cus.address_province addr_state,
        cus.address_postal_code addr_zip_code,
        dl.name
    from
        hive.rtm_analytics.l2_odhsb_sbv5_at_service_job_rs sj 
        join hive.rtm_analytics.l2_odhsb_sbv5_at_service_order_rs so on so.service_order_id = sj.service_order_id 
        join hive.rtm_analytics.l2_odhsb_sbv5_at_sj_part_rs sjp on sj.service_job_id = sjp.service_job_id
        join hive.rtm_analytics.l2_odhsb_sbv5_at_sa_retailer_store_rs rs on	sj.retailer_store_id = rs.retailer_store_id
        join hive.l2_retail.odhsb_sbv5_at_so_product sprd on sprd.service_order_id = so.service_order_id 
        join hive.l2_retail.odhsb_sbv5_at_sa_service_job_product_line sjpl on sjpl.sj_product_line_id = sprd.sj_product_line_id 
        join hive.l2_retail.odhsb_sbv5_st_txn_contact cus on cus.txn_id = sj.service_order_id and contact_type = 0
        left join hive.l2_retail.odhsb_sb_svbt_dispatch_zone z on sj.sj_zone_id = z.zone_id_char
        left join hive.l2_retail.odhsb_sb_svbt_dealer_location dl on z.dealer_location_id = dl.dealer_location_id
        left join (
            select
                entity_id,
                min(date_parse(old_value , '%%m/%%d/%%Y')) orig_sched_dt
            from
                hive.rtm_analytics.l2_odhsb_sbv5_st_audit_field_rs
            where
                owner_company_id = '43'
                and field_id = 'scheduledServiceDate'
                and cast(audit_date as date) >= date '2021-01-01'
            group by 1
        ) o on sj.service_job_id = o.entity_id
        left join (
            select 
                so.service_order_id,
                min(case when au.new_value = 'TAR' then au.audit_dateutc end) min_tech_arrival_dt,
                min(case when au.new_value in ('AAA','AWT','ACU','RTC','AAK','AAJ','ABB','ABC','ACP','ACQ','ACR','ACV') then au.audit_dateutc end) min_complete_dt
            from
                hive.rtm_analytics.l2_odhsb_sbv5_st_audit_field_rs au
                join rtm_analytics.l2_odhsb_sbv5_at_service_job_rs  sj on au.entity_id = sj.service_job_id
                join l2_retail.odhsb_sbv5_at_service_order so on so.service_order_id = sj.service_order_id
                join rtm_analytics.l2_odhsb_sbv5_at_txn_exception_rs e on e.txn_id = sj.service_job_id
                join rtm_analytics.l2_odhsb_sbv5_at_txn_exception_detail_rs ed on ed.exception_id  = e.exception_id and ed.exception_code = 'PRE_DIAGNOSIS'
            where
                au.owner_company_id = '43'
                and cast(au.audit_date as date) >= date '2021-01-01'
                and au.field_id = 'serviceJobSubStatus'
            group by
                so.service_order_id
        ) ftf on ftf.service_order_id = so.service_order_id
    where
        --exception_code = 'PRE_DIAGNOSIS'
    -- 	and payment_type = 'CASHONDELIVERY'
    -- and retailer_store_name = 'Major Appliance - Samsung'
    --sjpl.description IN ('HOME REFRIGERATION' , 'HOME LAUNDRY ELEC', 'HOME LAUNDRY GAS', 'DISHWASHER')
        cast(sj.scheduled_service_date as date) >= cast(date_add('month',-12,current_date) as date)
        and sj.service_provider_id in ('1133787699','1116738095','1115480731')
        and sj.service_job_status in ('CMP','ACC')
    """
    demand = pd.read_sql(sql, presto_connection)
    demand = demand[~demand.addr_zip_code.isna()]
    demand = demand[demand.addr_zip_code != 'UNKNOWN']
    demand['cust_zip'] = demand.addr_zip_code.str[:5]
    demand = demand[demand['cust_zip'].apply(lambda x: x.isnumeric())]
    demand['cust_zip'] = demand['cust_zip'].astype(int)

    return(demand)

In [12]:
def get_market_coverage():
    presto_connection =  atlas.Presto(environment = 'presto://{}:{}@atlas-workbench-presto.atlas.prd.aws.asurion.net:18443/hive').connect()
    coverage_sql = """
    select 
        com.name,
        sp.service_provider_id,
        dl.name location_name,
        atlasdecrypt(dl.address_line1_token) address,
        dl.address_city,
        dl.address_state,
        dl.address_zip,
        spl.service_provider_location_id,
        sjz.sj_zone_id,
        sjz.time_zone,
        cov.*
    from
        l2_retail.odhsb_sbv5_at_sa_service_provider sp 
        join hive.l2_retail.odhsb_sb_svbt_company com on sp.service_provider_id = com.company_id_char
        join l2_retail.odhsb_sbv5_at_service_provider_location spl on sp.service_provider_id = spl.service_provider_id 
        join hive.l2_retail.odhsb_sb_svbt_dealer_location dl on dl.dealer_location_id_char = spl.service_provider_location_id
    --  join l2_retail.odhsb_servicebenchv5_at_sj_first_avail_request far on 
        join l2_retail.odhsb_servicebenchv5_at_sp_service_job_zone sjz on sjz.service_provider_location_id = spl.service_provider_location_id 
    --    join hive.l2_retail.odhsb_servicebenchv5_at_sp_sj_zone_coverage_change sjzc on sjzc.sj_zone_id = sjz.sj_zone_id
        join hive.l2_retail.odhsb_servicebench_svbt_dealer_zone_coverage cov on cov.zone_id_char = sjz.sj_zone_id
    --    join l2_retail.odhsb_servicebench_svbt_dealer_loc_coverage dlc on cast(dlc.dealer_location_id as varchar)  = spl.service_provider_location_id 
    --  join l2_retail.odhsb_servicebench_svbt_manufacturer_dealer_loc mdl on mdl
    --    join l2_retail.odhsb_servicebenchv5_at_sp_sj_availability ssa on sjz.sj_zone_id = ssa.sj_zone_id 
    where 
        sp.service_administrator_id = '43'
    --    and sp.account_number = '0117521'
        --and com.name = 'ASURION REPAIR SERVICES'
        and sp.service_provider_id in ('1133787699','1116738095','1115480731')
        --and sjz.sj_zone_id = '1138146988'
    """
    coverage = pd.read_sql(coverage_sql, presto_connection)
    if coverage.shape[0] >0:
        print('Sucessfully read coverage per market')
        coverage['location_name'] = coverage['location_name'].str.lower()
        return(coverage)

In [13]:
def filter_market_coverage(market_name):
    coverage = get_market_coverage()
#     market_name = str.lower(market_name)
    coverage_for_market_name = coverage[coverage.location_name.isin(market_name)]
    return(coverage_for_market_name)
    

In [14]:
def determine_clust_centroids(model, dataset, level, cluster_number, clusters_centroids, clusters_radii):
    if level == 1:
        clusters_centroids=dict()
        clusters_radii= dict()        
    for cluster in list(range(model.n_clusters)):
#         print(cluster)
        if level == 1:
            key = str(cluster)
        else:
            key = str(cluster_number + cluster/10)
#         print(key)
        clusters_centroids[key]=list(zip(model.cluster_centers_[:, 0],model.cluster_centers_[:,1]))[cluster]
        clusters_radii[key] = max([haversine(i,clusters_centroids[key]) for i in list(zip(dataset[dataset.assigned_clusters == cluster]['lat'],dataset[dataset.assigned_clusters == cluster]['lon']))])
#         print(clusters_centroids)
    return(clusters_centroids,clusters_radii)

In [15]:
def apply_constraint_kmeans(num_of_clusters, size_min, size_max, df):
    clf = KMeansConstrained(
    n_clusters=num_of_clusters,
    size_min=size_min,
    size_max=size_max,
    random_state=0)
    
    return(clf.fit_predict(df[['lat','lon']]), clf)

def apply_kmeans(num_of_clusters, df):
    kmeans=KMeans(n_clusters=num_of_clusters, init='k-means++',random_state=0).fit(df[['lat','lon']])
    return(kmeans.fit_predict(df[['lat','lon']]), kmeans)

In [16]:
def analysis(lat1, long1, lat2, long2):
#     This function gets time taken to traven and distance between two points using OSRM package
# The server on ip 100.70.175.6 has to be started before executing code below. Please contact Suresh to turn it on. 
    time.sleep(3)
    url = 'http://100.70.175.6:5000/route/v1/driving/{},{};{},{}'
    r = requests.get(url.format(long1,lat1,long2,lat2)).text
    data = json.loads(r)
    try:
        distance = round(data["routes"][0]["distance"]*0.621371/1000, 1)
        duration = round(data["routes"][0]["duration"]/60, 1)
        return([distance,duration])
    except KeyError:
        return([-1.0,-1.0])

In [18]:
zip_df = gpd.read_file('C:/Users/ruta.deshmukh.NEW_STERLING/Desktop/All projects/MA_coverage/python notebooks/Archives/zip_level_shape_files/cb_2018_us_zcta510_500k.shp')
zip_df['ZCTA5CE10'] = zip_df['ZCTA5CE10'].astype(str)

def initialize_map(lat, lon, coverage):
    m = folium.Map(location=[lat,lon], zoom_start=8, overlay=True)
    zip_df_market = zip_df[zip_df.ZCTA5CE10.isin(coverage)]
    fg = folium.map.FeatureGroup('coverage').add_to(m)
    for _, r in zip_df_market.iterrows():
            # Without simplifying the representation of each borough,
            # the map might not be displayed
        sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
        geo_j = sim_geo.to_json()
        geo_j = folium.GeoJson(data=geo_j,
                                   style_function=lambda x: {'fillColor': 'orange'}, name = 'coverage')
        folium.Popup('coverage').add_to(geo_j)
        fg.add_child(geo_j)
    return(m)

In [19]:
url = 'http://100.70.180.199:8080/search'

def geocode_address(row):
    params = {
        'street': row.addr_line_1,
        'city': row.address_city,
        'state': row.addr_state,
        'postalcode': row.cust_zip
    }
    # print(params)
    res = requests.get(url, params=params)
    if res and res.json():
#         print('used adre, city, state')
        return [res.json()[0]['lat'], res.json()[0]['lon']]

#skipping city from parameters increases wrong cordinate rates
#     params = {
#         'street': row.addr_line_1,
#         'state': row.addr_state,
#         'postalcode': row.cust_zip
#     }
#     res = requests.get(url, params=params)
#     if res and res.json():
# #         print('street, state')
#         return [res.json()[0]['lat'], res.json()[0]['lon']]
    
    params = {
        'city': row.address_city,
        'state': row.addr_state,
        'postalcode': row.cust_zip
    }
    res = requests.get(url, params=params)
    if res and res.json():
#         print('city, state')
        return [res.json()[0]['lat'], res.json()[0]['lon']]

    params = {
        'street': row.addr_line_1,
        'city': row.address_city,
        'state': row.addr_state
    }
    res = requests.get(url, params=params)
    if res and res.json():
#         print('city, state')
        return [res.json()[0]['lat'], res.json()[0]['lon']]
    else:
        return 'error'

def geocode_zipcode(row):
    params = {
        'postalcode': row.cust_zip
    }
    # print(params)
    res = requests.get(url, params=params)
    if res and res.json():
#         print('used adre, city, state')
        return [res.json()[0]['lat'], res.json()[0]['lon']]
    else:
        return 'error'

In [20]:
# def get_centermost_point(cluster):
#     centroid = (MultiPoint(cluster).centroid.x, MultiPoint(cluster).centroid.y)
#     centermost_point = min(cluster, key=lambda point: great_circle(point, centroid).m)
#     centermost_point[0] = float(centermost_point[0])
#     centermost_point[1] = float(centermost_point[1])
# #     print(tuple(centermost_point))
#     return tuple(centermost_point)
# centermost_points = clusters.map(get_centermost_point)

In [21]:
def get_elbow_point(min_range, max_range, dataset):
    Sum_of_squared_distances = []
    K = range(1,10)
    for num_clusters in K :
        kmeans = KMeans(n_clusters=num_clusters)
        kmeans.fit(dataset)
        Sum_of_squared_distances.append([num_clusters, kmeans.inertia_])

    Sum_of_squared_distances = pd.DataFrame(Sum_of_squared_distances, columns = ['num_of_clusters','sse'])
#     print(Sum_of_squared_distances)
    kn = KneeLocator(Sum_of_squared_distances.num_of_clusters, Sum_of_squared_distances.sse, curve='convex', direction='decreasing')
    return(kn.knee)

### 1) Loading coverage and historical service job volume

In [22]:
demand = get_demand()

In [24]:
coverage = get_market_coverage()

Sucessfully read coverage per market


In [25]:
coverage.location_name.unique()

array(['asurion major appliance repair', 'fort lauderdale',
       'des moines-oem', 'portland', 'jacksonville', 'inactive',
       'memphis-oem', 'san antonio-oem', 'nashville-oem', 'san diego-oem',
       'asurion major appliance la', 'pittsburgh-oem', 'miami',
       'new orleans-oem', 'riverside-oem', 'daytona', 'saint louis-oem',
       'ocala', 'jupiter', 'grand rapids', 'kansas city-oem', 'orlando',
       'rochester', 'sacramento-oem', 'dallas-oem', 'palm springs',
       'alexandria-oem', 'long island west', 'pittsburgh', 'raleigh-oem',
       'indianapolis-oem', 'oklahoma city-oem', 'tallahassee',
       'san jose-oem', 'long island east', 'chattanooga', 'tampa',
       'chicago-oem', 'alexandria', 'charleston-oem', 'cleveland-oem',
       'boston', 'long island-oem', 'atlanta-oem', 'minneapolis-oem',
       'denver-oem', 'syracuse', 'seattle', 'columbus oh-oem',
       'los angeles-oem', 'fort myers', 'long beach-oem',
       'asurion repair services', 'houston-oem', 'odessa

In [26]:
coverage_orlando = filter_market_coverage(['tampa'])

Sucessfully read coverage per market


In [27]:
demand_market = demand[demand.name.isin(['TAMPA'])]
demand_market = demand_market[['service_order_id','service_order_number','crm_number','service_job_number','addr_line_1', 'address_city', 'addr_state', 'addr_zip_code', 'name','cust_zip']].drop_duplicates()
demand_market = demand_market.groupby(['service_order_id','service_order_number'])[['addr_line_1','address_city','addr_state','cust_zip']].max().reset_index()

In [28]:
demand_market['cust_adr_lat_lon'] = demand_market.apply(geocode_address, axis = 1)
demand_market[demand_market.cust_adr_lat_lon == 'error'].shape
demand_market = demand_market[demand_market.cust_adr_lat_lon != 'error']
demand_market['lat'] = demand_market['cust_adr_lat_lon'].apply(lambda x: x[0])
demand_market['lon'] = demand_market['cust_adr_lat_lon'].apply(lambda x: x[1])
demand_market[['lat','lon']] = demand_market[['lat','lon']].astype(float)

In [29]:
# demand_market = pd.read_csv('orlando_dataset.csv', sep = '|')

In [30]:
# Getting tech home locations 
tech_locations= pd.read_excel('tampa_tech_home_locations.xlsx')

In [31]:
tech_locations['addr_line_1'] = tech_locations['Home Address'].apply(lambda x: x.split(',')[0])
tech_locations['address_city'] = tech_locations['Home Address'].apply(lambda x: x.split(',')[1])
tech_locations['addr_state'] = tech_locations['Home Address'].apply(lambda x: x.split(',')[2][0:3])
tech_locations['cust_zip'] = tech_locations['Home Address'].apply(lambda x: x.split(',')[2][-5:])

tech_locations['adr_lat_lon'] = tech_locations.apply(geocode_address, axis = 1)
tech_locations['lat'] = tech_locations['adr_lat_lon'].apply(lambda x: x[0])
tech_locations['lon'] = tech_locations['adr_lat_lon'].apply(lambda x: x[1])
tech_locations = tech_locations[tech_locations.adr_lat_lon != 'error']
number_of_techs = tech_locations[tech_locations.Skill != 'senior'].shape[0]

In [32]:
number_of_techs

17

### 2) Applying Dbscan to identify outliers

In [33]:
from sklearn.cluster import DBSCAN
from geopy.distance import great_circle
from shapely.geometry import MultiPoint
# df = pd.read_csv(demand_orlando'summer-travel-gps-full.csv')
coords = demand_market[['lat', 'lon']].to_numpy()


In [34]:
# Higher value of min_samples results in more outliers

miles_per_radian = 3958.7613
epsilon = 5 / miles_per_radian
db = DBSCAN(eps=epsilon, min_samples=80, algorithm='ball_tree', metric='haversine').fit(np.radians(coords))
cluster_labels = db.labels_
num_clusters = len(set(cluster_labels))
clusters = pd.Series([coords[cluster_labels == n] for n in list(set(cluster_labels))])
print('Number of clusters: {}'.format(num_clusters))

Number of clusters: 4


In [35]:
demand_market['assigned_clusters'] = cluster_labels

In [36]:
demand_market_nooutliers = demand_market[demand_market['assigned_clusters'] != -1]

In [37]:
demand_market_nooutliers[['lat', 'lon']] = demand_market_nooutliers[['lat', 'lon']].astype(float)

In [38]:
# Find optimum number level 1 clusters in dataset using elbow point
number_of_clusters_level1 = get_elbow_point(1,15,demand_market_nooutliers[['lat','lon']])

In [52]:
demand_market_nooutliers['assigned_clusters_level1']

service_order_id service_order_number                  addr_line_1  \
0          SO39240298         SNWP4256C26A     2237 HIDDEN MEADOWS DR E   
1          SO39270559         SNWP4257389F             8830 SENTIERO DR   
2          SO39281305         SNWP42576299              7204 Grand Blvd   
3          SO39282012         SNWP4257655C               17129 Downs Dr   
4          SO39289493         SNWP42578295           2467 LUNA CREST CT   
...               ...                  ...                          ...   
3014       SO46358980         SNWQ12C361C4            5304 Windbrush Dr   
3015       SO46358994         SNWQ12C361D2            617 Centerwood Dr   
3016       SO46359795         SNWQ12C364F3          9129 FOX SPARROW RD   
3017       SO46368891         SNWQ12C3887B        8842 Cameron Crest Dr   
3019       SO46385253         SNWQ12C3C865  23848 PLANTATION PALMS BLVD   

         address_city addr_state  cust_zip  \
0         PALM HARBOR         FL     34683   
1       LAND O' LAKES         FL     34637   
2     New Port Richey         FL     34652   
3              Odessa         FL     33556   
4         ZEPHYRHILLS         FL     33543   
...               ...        ...       ...   
3014            Tampa         FL     33625   
3015   Tarpon Springs         FL     34688   
3016            Tampa         FL     33626   
3017            Tampa         FL     33626   
3019     Land O Lakes         FL     34639   

                              cust_adr_lat_lon        lat        lon  \
0                      [28.072987, -82.745753]  28.072987 -82.745753   
1                    [28.2188992, -82.4575938]  28.218899 -82.457594   
2                    [28.2347778, -82.7232999]  28.234778 -82.723300   
3                 [28.183222, -82.55402792188]  28.183222 -82.554028   
4                    [28.2336196, -82.1811947]  28.233620 -82.181195   
...                                        ...        ...        ...   
3014                  [27.9477595, -82.458444]  27.947760 -82.458444   
3015  [28.148082950000003, -82.74380159717906]  28.148083 -82.743802   
3016                  [27.9477595, -82.458444]  27.947760 -82.458444   
3017                  [27.9477595, -82.458444]  27.947760 -82.458444   
3019                 [28.2058582, -82.4308397]  28.205858 -82.430840   

      assigned_clusters color_level1  assigned_clusters_level1  
0                     1      #FDD49E                         1  
1                     0      #FEF0D9                         0  
2                     1      #FDD49E                         1  
3                     1      #FDD49E                         1  
4                     0      #FEF0D9                         0  
...                 ...          ...                       ...  
3014                  3      #FFFFD4                         3  
3015                  1      #FDD49E                         1  
3016                  3      #FFFFD4                         3  
3017                  3      #FFFFD4                         3  
3019                  0      #FEF0D9                         0  

[2854 rows x 12 columns]

### 3) Apply level 1 clustering using kmeans. 
#### This step identifies high level clusters by finding elbow curve point in range 0 to15

In [39]:
demand_market_nooutliers['assigned_clusters'], kmeans_clf = apply_kmeans(number_of_clusters_level1,demand_market_nooutliers)
clusters_centroids_kmeans = {}
clusters_radii_kmeans = {}
clusters_centroids_kmeans, clusters_radii_kmeans = determine_clust_centroids(kmeans_clf, demand_market_nooutliers, 1, 1, clusters_centroids_kmeans ,clusters_radii_kmeans)

In [40]:
demand_market_nooutliers['color_level1'] = color_scheme.assign_color(demand_market_nooutliers.assigned_clusters, mapping)

In [43]:
def cluster_stats(dataset, centroid_dict, number_of_techs):
    tablular_analysis_clusters = pd.DataFrame()
    for rec in dataset.assigned_clusters.unique():
        Cluster_df = dataset[dataset.assigned_clusters == rec]
        Cluster_df['distance_from_centroid'] = dist_from_centroid(Cluster_df, centroid_dict[str(rec)])
        tablular_analysis = pd.DataFrame()
        tablular_analysis['assigned_clusters_level1'] = Cluster_df.assigned_clusters.unique()
        tablular_analysis['cluster number'] = Cluster_df.assigned_clusters.unique()
        tablular_analysis['claim volume in cluster'] = Cluster_df.shape[0]
        tablular_analysis['% claims in cluster'] = round((Cluster_df.shape[0]/dataset.shape[0])*100)
        tablular_analysis['number_of_techs'] = round((tablular_analysis['% claims in cluster']*number_of_techs)/100)
        tablular_analysis['weighted avg driving distance'] = round(average( Cluster_df['distance_from_centroid']),2)
        tablular_analysis['farthest point in cluster'] = Cluster_df[Cluster_df.distance_from_centroid == Cluster_df.distance_from_centroid.max()]['distance_from_centroid'].values[0]
        tablular_analysis_clusters = tablular_analysis_clusters.append(tablular_analysis)
    return(tablular_analysis_clusters)

level1_clustering_stats = cluster_stats(demand_market_nooutliers, clusters_centroids_kmeans, number_of_techs)

### 4) Apply level 2 clustering using constraint kmeans

In [45]:
demand_market_nooutliers['assigned_clusters_level1'] = demand_market_nooutliers['assigned_clusters']
df_level2_clusters = pd.DataFrame()
tabular_analysis_level2 = pd.DataFrame()
for index, each in level1_clustering_stats.iterrows():
    if each.number_of_techs >1:
        df = demand_market_nooutliers[demand_market_nooutliers.assigned_clusters_level1 == each['assigned_clusters_level1']]
        max_size = round(df.shape[0]/each.number_of_techs)+10
        min_size = 10
        num_of_techs = each.number_of_techs.astype(int)
        cluster_number = df.assigned_clusters_level1.unique()[0]
        
        df['assigned_clusters'], clf = apply_constraint_kmeans(num_of_techs, min_size,max_size,df )
        clusters_centroids_constraint_kmeans, clusters_radii_constraint_kmeans = determine_clust_centroids(clf, df, 2, cluster_number, clusters_centroids_kmeans, clusters_radii_kmeans)
        
        #Change cluster naming after determining centroids
        df['assigned_clusters'] = df['assigned_clusters_level1'] + df['assigned_clusters']/10
        tabular_analysis_level2 = tabular_analysis_level2.append(cluster_stats(df, clusters_centroids_constraint_kmeans,1))
        df_level2_clusters = df_level2_clusters.append(df)

In [46]:
tabular_analysis_level2['centroid_lat'] = tabular_analysis_level2.apply(lambda x: clusters_centroids_constraint_kmeans[str(x.assigned_clusters_level1)][0], axis = 1)
tabular_analysis_level2['centroid_lon'] = tabular_analysis_level2.apply(lambda x: clusters_centroids_constraint_kmeans[str(x.assigned_clusters_level1)][1], axis = 1)

In [47]:
tech_locations_bkp = tech_locations.reset_index()
assigned_techs = pd.DataFrame()
for index, each in tabular_analysis_level2.iterrows():
    l = function_distance(tech_locations_bkp,(each.centroid_lat, each.centroid_lon))
    if len(l)>0:
        tech_indx = l.index(min(l))
        assigned_techs = assigned_techs.append([tech_locations_bkp[tech_locations_bkp.index==tech_indx][['Name','Home Address']]])
        tech_locations_bkp = tech_locations_bkp.drop(index = tech_indx).reset_index(drop=True)
    else:
        assigned_techs.append([])

In [48]:
tabular_analysis_level2['assigned_tech_name'] = assigned_techs['Name'].values
tabular_analysis_level2['Home Address'] = assigned_techs['Home Address'].values

In [108]:
# def create_mapping():
color_schemes = pd.read_csv('color_list_folium.csv', sep = '|')
color_schemes['cluster_num'] = np.arange(0.0, 11.0, 0.1)[:-3]
color_schemes['cluster_num'] = color_schemes['cluster_num'].apply(lambda x: round(x, 1))
# color_schemes['cluster_num'] = color_schemes['cluster_num'].astype(str)
mapping = dict(color_schemes[['cluster_num', 'color']].values)
#     return mapping

def assign_color(col, mapping):
    color_selected = col.map(mapping)
    return color_selected

In [112]:
df_level2_clusters['color_level2'] = assign_color(df_level2_clusters.assigned_clusters, mapping)

### 5) Plotting clusters on map

In [156]:

m_level1 = initialize_map(demand_market_nooutliers.lat.iloc[0],demand_market_nooutliers.lon.iloc[0], coverage_orlando.coverage_zip_code)
HeatMap(demand_market[['lat','lon']], name = 'Claim Volume').add_to(m_level1)

fg_clusters = folium.map.FeatureGroup('level1_clusters').add_to(m_level1)
for lt, ln, color in zip(demand_market_nooutliers.lat, demand_market_nooutliers.lon, demand_market_nooutliers.color_level1):
    cm = folium.CircleMarker(location=[lt, ln],
                            radius = 6,
#                             popup=str(el)+" m",
                            fill=True, # Set fill to True
                            fill_color=color,
                            color = color,
                            fill_opacity=0.7,
                            line_opacity=0.7,
                            name = 'Clusters',
                            control=True)
    fg_clusters.add_child(cm)

In [157]:
fg_techs = folium.map.FeatureGroup('Tech Assigned Locations').add_to(m_level1)
for lt, ln, skill, tech_name in zip(tabular_analysis_level2.centroid_lat, tabular_analysis_level2.centroid_lon, tech_locations.Skill, tabular_analysis_level2.assigned_tech_name):
#     print(tech_name)
    if skill == 'senior':
        cm = folium.Marker(location=[lt, ln],
                           popup = tech_name,
                           icon=folium.Icon(color='blue', icon='male', prefix='fa'))
    else:
        cm = folium.Marker(location=[lt, ln],
                            popup = tech_name,
                           icon=folium.Icon(color='lightgray', icon='male', prefix='fa'))
    fg_techs.add_child(cm)

In [158]:
for each in df_level2_clusters.assigned_clusters_level1.unique():
    plot_df = df_level2_clusters[df_level2_clusters.assigned_clusters_level1 == each]
    fg_clusters = folium.map.FeatureGroup('level2_cluster{}'.format(plot_df.assigned_clusters_level1.values[0])).add_to(m_level1)
    for lt, ln, color in zip(plot_df.lat, plot_df.lon, plot_df.color_level2):
        cm = folium.CircleMarker(location=[lt, ln],
                                radius = 6,
    #                             popup=str(el)+" m",
                                fill=True, # Set fill to True
                                fill_color=color,
                                color = color,
                                fill_opacity=0.7,
                                line_opacity=0.7,
                                name = 'clusters',
                                control=True)
        fg_clusters.add_child(cm)

In [159]:
# Adding layer controls to select which layers to display
folium.LayerControl().add_to(m_level1)

In [160]:
m_level1

In [161]:
m_level1.save('Maps/tampa/tech_assigned_v2.html')

In [168]:
params = {
#         'street': '10422 GLEN WILLOW LN',
#         'city': 'Tampa',
#         'state': 'FL',
        'postalcode': '33647'
    }
    # print(params)
res = requests.get(url, params=params)

In [169]:
res.json()

[{'place_id': 13008221,
  'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
  'boundingbox': ['27.962126766444',
   '28.282126766444',
   '-82.514370541056',
   '-82.194370541056'],
  'lat': '28.12212676644359',
  'lon': '-82.35437054105648',
  'display_name': 'Tampa, Hillsborough County, Florida, 33647, United States',
  'place_rank': 21,
  'category': 'place',
  'type': 'postcode',
  'importance': 0.33499999999999996}]

In [288]:
# df_level2_clusters.to_csv('orlando_dataset_with_labels.csv', sep = '|')

In [131]:
df_level2_clusters[df_level2_clusters.assigned_clusters == 3.0]

service_order_id service_order_number               addr_line_1  \
676        SO42031683         SNWP72815A43      10422 GLEN WILLOW LN   
687        SO42039720         SNWP728179A8      10501 CASTLEFORD WAY   
695        SO42047832         SNWP72819958      9616 GRETNA GREEN DR   
699        SO42055084         SNWP7281B5AC          15150 NIGHT HAWK   
703        SO42059118         SNWP7281C56E        4506 GOLDWOOD BVLD   
...               ...                  ...                       ...   
2286       SO45361606         SNWPC2B429C6  11311 QUIET FOREST DRIVE   
2294       SO45368902         SNWPC2B44646       10504 BARNSTABLE CT   
2295       SO45369893         SNWPC2B44A25      4834 Bonita Vista Dr   
2298       SO45374637         SNWPC2B45CAD          8221 Malvern Cir   
2307       SO45382395         SNWPC2B47AFB      14316 Arbor Hills Rd   

     address_city addr_state  cust_zip          cust_adr_lat_lon       lat  \
676         Tampa         FL     33647  [27.9477595, -82.458444]  27.94776   
687         Tampa         FL     33626  [27.9477595, -82.458444]  27.94776   
695         Tampa         FL     33626  [27.9477595, -82.458444]  27.94776   
699         Tampa         FL     33625  [27.9477595, -82.458444]  27.94776   
703         Tampa         FL     33634  [27.9477595, -82.458444]  27.94776   
...           ...        ...       ...                       ...       ...   
2286        Tampa         FL     33635  [27.9477595, -82.458444]  27.94776   
2294        Tampa         FL     33626  [27.9477595, -82.458444]  27.94776   
2295        Tampa         FL     33634  [27.9477595, -82.458444]  27.94776   
2298        Tampa         FL     33634  [27.9477595, -82.458444]  27.94776   
2307        Tampa         FL     33625  [27.9477595, -82.458444]  27.94776   

            lon  assigned_clusters color_level1  assigned_clusters_level1  \
676  -82.458444                3.0      #FFFFD4                         3   
687  -82.458444                3.0      #FFFFD4                         3   
695  -82.458444                3.0      #FFFFD4                         3   
699  -82.458444                3.0      #FFFFD4                         3   
703  -82.458444                3.0      #FFFFD4                         3   
...         ...                ...          ...                       ...   
2286 -82.458444                3.0      #FFFFD4                         3   
2294 -82.458444                3.0      #FFFFD4                         3   
2295 -82.458444                3.0      #FFFFD4                         3   
2298 -82.458444                3.0      #FFFFD4                         3   
2307 -82.458444                3.0      #FFFFD4                         3   

     color_level2  
676       #FFFFCC  
687       #FFFFCC  
695       #FFFFCC  
699       #FFFFCC  
703       #FFFFCC  
...           ...  
2286      #FFFFCC  
2294      #FFFFCC  
2295      #FFFFCC  
2298      #FFFFCC  
2307      #FFFFCC  

[172 rows x 13 columns]

In [287]:
df_level2_clusters.columns = ['Unnamed: 0', 'service_order_id', 'service_order_number', 'addr_line_1',
       'address_city', 'addr_state', 'cust_zip', 'cust_adr_lat_lon', 'lat',
       'lon', 'assigned_clusters__level2', 'color_level1', 'assigned_clusters_level1',
       'color_level2']

In [134]:
tabular_analysis_level2.to_excel('Maps/tampa/cluster_stats_tech_assigned.xlsx')